In [4]:
import os
import sys
import torch
import torch.backends.cudnn as cudnn
from os import path, mkdir
import logging
from torch.utils.tensorboard import SummaryWriter

module_path = os.path.abspath(os.path.join(".."))
if module_path not in sys.path:
    sys.path.append(module_path)

from feature_extractor import FeaturesWriter, get_features_loader
from utils.utils import register_logger
from utils.load_model import load_feature_extractor
from features_loader import FeaturesLoader
from network.TorchUtils import TorchModel
from network.anomaly_detector_model import (
    AnomalyDetector,
    custom_objective,
    RegularizedLoss,
)
from utils.callbacks import DefaultModelCallback, TensorBoardCallback

In [48]:
def get_torch_device():
    return "cuda" if torch.cuda.is_available() else "cpu"
    # device = "cpu"

# Definitions

## Global definitions

In [49]:
log_every = 50  # log the writing of clips every n steps
log_file = r"C:\Users\HS TRADER\Downloads\Thesis_Code\AnomalyDetectionCVPR2018-Pytorch\log.log"  # set logging file
num_workers = 2  # define the number of workers used for loading the videos

cudnn.benchmark = True
register_logger(log_file=log_file)

device = get_torch_device()  # will use GPU if available, CPU otherwise

## Definitions of features extraction

In [ ]:
dataset_path = r"C:\Users\HS TRADER\Downloads\Thesis_Code\dataset\training"  # path to the video dataset
clip_length = 16  # define the length of each input sample
frame_interval = 1  # define the sampling interval between frames
features_dir = r"C:\Users\HS TRADER\Downloads\Thesis_Code\AnomalyDetectionCVPR2018-Pytorch\features\c3d\training_c3d"  # set directory for the features
batch_size = 2

model_type = "c3d"
pretrained_3d = r"C:\Users\HS TRADER\Downloads\Thesis_Code\AnomalyDetectionCVPR2018-Pytorch\pretrained\c3d.pickle"  # set the path of the 3d feature extractor

# model_type = "mfnet"
# pretrained_3d = r"C:\Users\HS TRADER\Downloads\Thesis_Code\AnomalyDetectionCVPR2018-Pytorch\pretrained\MFNet3D_UCF-101_Split-1_96.3.pth"  # set the path of the 3d feature extractor

## Definitions of training

In [ ]:
annotation_path = r"C:\Users\HS TRADER\Downloads\Thesis_Code\AnomalyDetectionCVPR2018-Pytorch\Train_Annotation.txt"  # path to train annotation
exps_dir = r"C:\Users\HS TRADER\Downloads\Thesis_Code\AnomalyDetectionCVPR2018-Pytorch\exps\c3d"  # path to the directory where models and tensorboard would be saved
feature_dim = 4096
save_every = 25  # epochs interval for saving the model checkpoints
lr_base = 0.01  # learning rate
iterations_per_epoch = 5000  # number of training iterations
epochs = 1  # number of training epochs


models_dir = path.join(exps_dir, "models")
tb_dir = path.join(exps_dir, "tensorboard")

os.makedirs(exps_dir, exist_ok=True)
os.makedirs(models_dir, exist_ok=True)
os.makedirs(tb_dir, exist_ok=True)

# Features Extraction

## Create model and dataset

In [52]:
data_loader, data_iter = get_features_loader(
    dataset_path, clip_length, frame_interval, batch_size, num_workers, model_type
)

network = load_feature_extractor(model_type, pretrained_3d, device).eval()

features_writer = FeaturesWriter(num_videos=data_loader.video_count)

2025-04-15 18:58:11,633 Found 765 video files in C:\Users\HS TRADER\Downloads\Thesis_Code\dataset\training


100%|██████████| 48/48 [08:12<00:00, 10.25s/it]

2025-04-15 19:06:23,895 Loading feature extractor from C:\Users\HS TRADER\Downloads\Thesis_Code\AnomalyDetectionCVPR2018-Pytorch\pretrained\c3d.pickle


In [53]:
if not path.exists(features_dir):
    # mkdir(features_dir)
    os.makedirs(features_dir, exist_ok=True)

In [ ]:
loop_i = 0
with torch.no_grad():
    for data, clip_idxs, dirs, vid_names in data_iter:
        if data is None:
            continue  # skip if batch is None (due to safe_collate)

        # ✅ PRINT SHAPE HERE
        print(f"[DEBUG] Clip batch shape: {data.shape}")
        outputs = network(data.to(device)).detach().cpu().numpy()

        for i, (dir, vid_name, clip_idx) in enumerate(zip(dirs, vid_names, clip_idxs)):
            if loop_i == 0:
                logging.info(
                    f"Video {features_writer.dump_count} / {features_writer.num_videos} : Writing clip {clip_idx} of video {vid_name}"
                )

            loop_i += 1
            loop_i %= log_every  # ✅ Replace args.log_every with log_every

            dir = path.join(features_dir, dir)  # ✅ Replace args.save_dir with features_dir
            features_writer.write(
                feature=outputs[i],
                video_name=vid_name,
                idx=clip_idx,
                dir=dir,
            )

features_writer.dump()

In [ ]:
features_writer.dump(features_dir)

2025-03-28 16:39:23,849 765 / 765:	Dumping C:\Users\HS TRADER\Downloads\Thesis_Code\AnomalyDetectionCVPR2018-Pytorch\features\wrongway\Wrongway128_x264.txt


# Train the Anomaly Detection Model Using the Extracted Features

## Create model, dataset, optimizer and loss function

In [ ]:
train_loader = FeaturesLoader(
    features_path=features_dir,
    annotation_path=annotation_path,
    iterations=iterations_per_epoch,
)

network = AnomalyDetector(feature_dim)  # ✅ Replaced args.feature_dim with feature_dim
model = TorchModel(network).to(device).train()

# Callbacks
model.register_callback(DefaultModelCallback(visualization_dir=exps_dir))  # ✅ Replaced args.exps_dir with exps_dir
model.register_callback(TensorBoardCallback(tb_writer=SummaryWriter(log_dir=tb_dir)))

# Training parameters
"""
In the original paper:
    lr = 0.01
    epsilon = 1e-8
"""
optimizer = torch.optim.Adadelta(model.parameters(), lr=lr_base, eps=1e-8)  # ✅ Replaced args.lr_base with lr_base

criterion = RegularizedLoss(network, custom_objective).to(device)

## Train the model

In [ ]:
model.fit(
    train_iter=train_loader,
    criterion=criterion,
    optimizer=optimizer,
    epochs=epochs,
    network_model_path_base=models_dir,
    save_every=save_every,
)

2025-03-29 04:52:38,074 Training for 100 epochs
2025-03-29 04:53:13,354 Epoch 0/100      Iteration 0/5000    loss: 1.0468065738677979    Time: 35.274 seconds/iteration
2025-03-29 04:56:19,401 Epoch 0/100      Iteration 10/5000    loss: 1.0404175519943237    Time: 20.12 seconds/iteration
2025-03-29 04:57:40,901 Epoch 0/100      Iteration 20/5000    loss: 1.0404144525527954    Time: 14.42 seconds/iteration
2025-03-29 04:58:10,751 Epoch 0/100      Iteration 30/5000    loss: 1.0406311750411987    Time: 10.731 seconds/iteration
2025-03-29 04:58:28,425 Epoch 0/100      Iteration 40/5000    loss: 1.0369164943695068    Time: 8.545 seconds/iteration
2025-03-29 04:58:35,855 Epoch 0/100      Iteration 50/5000    loss: 1.0363523960113525    Time: 7.015 seconds/iteration
2025-03-29 04:58:39,979 Epoch 0/100      Iteration 60/5000    loss: 1.0389776229858398    Time: 5.933 seconds/iteration
2025-03-29 04:58:42,849 Epoch 0/100      Iteration 70/5000    loss: 1.0386719703674316    Time: 5.138 seconds/i